Install Textworld-Express and Graphviz visualization tool

In [22]:
!pip install textworld-express
!pip install graphviz
!pip install pydot

Import packages

In [23]:
from textworld_express import TextWorldExpressEnv
import graphviz
import pydot
from IPython.display import Image
import matplotlib.pyplot as plt
from collections import namedtuple
import re
import copy
import json
import math
import random

# Load game

I find this to be a good seed for experimenting.

In [24]:
SEED = 3

Create the environment wrapper. Currently creating a world with 5 locations, doors, and no distractor objects. Coin collecting game.

In [25]:
# Initialize game generator
ENV = TextWorldExpressEnv(envStepLimit=100)

# Set the game generator to generate a particular game (cookingworld, twc, or coin)
ENV.load(gameName="coin", gameParams="numLocations=5,includeDoors=1,numDistractorItems=0")

Reset the game

In [26]:
obs, infos = ENV.reset(seed=SEED, gameFold="train", generateGoldPath=True)
print(obs)

You are in the kitchen. In one part of the room you see a stove. There is also an oven. You also see a fridge that is closed. In another part of the room you see a counter, that has nothing on it. In one part of the room you see a kitchen cupboard that is closed. There is also a cutlery drawer that is closed. You also see a trash can that is closed. In another part of the room you see a dishwasher that is closed. In one part of the room you see a dining chair, that has nothing on it. 
To the South you see a closed sliding patio door. To the West you see a closed frosted-glass door. 


# Examples of actions

Get the valid actions available to the agent

In [27]:
validActions = infos['validActions']
print(validActions)

['look around', 'close door to west', 'move west', 'open door to south', 'open door to west', 'inventory', 'move south', 'close door to south']


Choose a random action and execute it

In [28]:
randomAction = random.choice(validActions)
print(randomAction)
obs, reward, done, infos = ENV.step(randomAction)
print(obs)

open door to west
You open the frosted-glass door, revealing the pantry. 


# Get the gold action sequence

Gold path is correct but not optimal.



In [29]:
gold = ENV.getGoldActionSequence()
print("GOLD", gold, '\n')

GOLD ['look around', 'open door to south', 'open door to west', 'move south', 'open door to east', 'move north', 'move south', 'move north', 'move west', 'move east', 'move south', 'move east', 'take coin'] 



# Build a map

State space data structure. State will be a tuple with two elements:
- id: a unique identifier for the state (an integer)
- observation: the text that accompanies the state. This will include the room description and inventory.

You can access a state like this:

```
s = State(id=1, observation="In a room")
s.id
s.observation
```

In [30]:
State = namedtuple("State", ['id', 'observation'])

Helper functions

**TODO**: need to pass env into look_at_inventory, obs_with_inventory, don't use global.

In [31]:
### Run the 'inventory' action and return the text generated by the game engine.
def look_at_inventory(env):
  obs, reward, done, infos = env.step('inventory')
  return obs

### Add the inventory to the world observation text.
### This gives a more complete text observation.
def obs_with_inventory(obs, env):
  return obs + '\n' + look_at_inventory(env)

### Pull the inventory items out of the observation text that includes
### the inventory (from obs_with_inventory())
def obs_inventory(obs):
  m = re.search(r'Inventory[a-zA-Z0-9 \(\)]*:\s*([a-zA-Z0-9 \.]+)', obs)
  if m is not None:
    if 'empty' not in m.group(1):
      return m.group(1)
  return 'empty'

### Pull the location out of the observation text.
def obs_location(obs):
  return obs.split('.')[0].split(' ')[-1]

In [32]:
### Get the valid actions that are only the movement actions.
def filter_actions_for_mapper(valid_actions):
  return list(filter(lambda a:'move' in a, valid_actions))

### Movement actions are reversable. North is the reverse of south, for example.
def reverse_action(act):
  reverse = {'move north': 'move south',
             'move south': 'move north',
             'move east': 'move west',
             'move west': 'move east'}
  if act in reverse:
    return reverse[act]
  else:
    return None

### Make the state for the mapper.
### Use the observation with inventory added.
def make_state_mapper(obs, env):
  modified_obs = obs_with_inventory(obs, env)
  return State(id=obs_to_id(modified_obs), observation=modified_obs)

### Reset the mapper. Return the initial observation and the valid actions.
def reset_mapper(env):
  # Reset environment
  obs, infos = env.reset(seed=SEED, gameFold="train", generateGoldPath=True)
  valid_actions = infos['validActions']
  # Close all the doors
  for act in valid_actions:
    if 'close door' in act:
      print("close door:", act)
      obs, reward, done, infos = env.step(act)
  closed_obs, reward, done, infos = env.step('look around')
  # Open all the doors
  for act in valid_actions:
    if 'open door' in act:
      obs, reward, done, infos = env.step(act)
  # Do look action
  obs, reward, done, infos = env.step('look around')
  # make the state from the observation text
  state = make_state_mapper(closed_obs, env)
  # Keep only move actions
  valid_actions = filter_actions_for_mapper(valid_actions)
  return state, valid_actions

### Compute an unique identifier for an observation.
### Use this as a unique state ID
def obs_to_id(obs):
  return abs(hash(obs)) # Technically the abs violates the hash uniqueness, but graphviz doesn't like dashes from negative numbers

### Do an action for the mapper.
### Run the state.
### Open all the doors
### Do a look action, and use use this observation text.
### Also return all the movement actions as valid actions.
def do_action_mapper(action, env):
  # Execute the step
  original_obs, reward, done, infos = env.step(action)
  valid_actions = infos['validActions']
  # Close all the doors
  for act in valid_actions:
    if 'close door' in act:
      print("close door:", act)
      obs, reward, done, infos = env.step(act)
  closed_obs, reward, done, infos = env.step('look around')
  # Open all the doors
  for act in valid_actions:
    if 'open door' in act:
      print("open door:", act)
      obs, reward, done, infos = env.step(act)
  # Do the look action
  obs, reward, done, infos = env.step('look around')
  # make the state from the observation text
  state = make_state_mapper(closed_obs, env)
  # Keep only the move actions
  valid_actions = filter_actions_for_mapper(valid_actions)
  return state, valid_actions

In [33]:
def change_coordinates(coordinates, action):
  if 'move' in action:
    dir = action.split()[1]
    if dir == 'north':
      return (coordinates[0], coordinates[1]+1)
    elif dir == 'south':
      return (coordinates[0], coordinates[1]-1)
    elif dir == 'east':
      return (coordinates[0]+1, coordinates[1])
    elif dir == 'west':
      return (coordinates[0]-1, coordinates[1])
  return coordinates

A depth-first search of the game map

In [34]:
def mapper(env):
  world_map = [] #list of directed edges between locations (direction via action label)
  world_map_hash_table = {}
  coordinates_hash = {} # maps locations to coordinates
  state, valid_actions = reset_mapper(env)
  mapper_aux(state, env, valid_actions, world_map, world_map_hash_table, coordinates_hash)
  return world_map, world_map_hash_table, coordinates_hash

In [11]:
def mapper_aux(state, env, valid_actions, world_map, world_map_hash_table, coordinates_hash,
               parent_id = None, action_performed = None, depth = 0, coordinates = (0,0)):
  print("state:", obs_location(state.observation), '-- depth:', depth)
  # We will be updating these globals:
  #global world_map_hash_table
  #global world_map
  # get id of new state---use the location
  id = obs_location(state.observation)
  coordinates_hash[id] = coordinates
  # Remember the observation that goes with this location
  world_map_hash_table[id] = state.observation # map location to observation
  # Record transition if this is not the first call to mapper
  if action_performed is not None and parent_id is not None:
    world_map.append((parent_id, action_performed, id)) 
    world_map.append((id, reverse_action(action_performed), parent_id))
  # If there is one action and this is not the first call to mapper,
  # then we are are in a dead-end and this is our base case.
  print("actions:", valid_actions)
  if len(valid_actions) == 1 and parent_id is not None and action_performed is not None:
    # base case
    # Return to parent by reversing the action just performed
    print("base case")
    r_action = reverse_action(action_performed)
    if r_action is not None:
      print("return to previous")
      temp_state, _ = do_action_mapper(r_action, env)
      print("now at", obs_location(temp_state.observation))
  else:
    # Not base case
    # Iterate through all the move actions
    for act in valid_actions:
      new_coordinates = change_coordinates(coordinates, act)
      print("try", act)
      # move out from current state to successor
      # but only if this is the first call to mapper or we are not
      # backtracking.
      if action_performed is None or act != reverse_action(action_performed): #short circuit on null action
        new_state, new_valid_actions = do_action_mapper(act, env)
        new_id = obs_location(new_state.observation)
        # Recurse!
        mapper_aux(new_state, env, new_valid_actions,
                   world_map, world_map_hash_table, coordinates_hash,
                   coordinates = new_coordinates,
                   parent_id = id, action_performed = act, depth = depth + 1)
      else:
        print("nope, don't return to parent")
    # We are returning up the recursive stack after trying every move action
    # Return to the parent
    if action_performed is not None:
      r_action = reverse_action(action_performed)
      if r_action is not None:
        print("return to parent")
        temp_state, _ = do_action_mapper(r_action, env)
        print('now at', obs_location(temp_state.observation))

Funtion for rendering the map to a .png image

In [20]:
def render_map(world_map, world_map_observations, filename = 'map'):
  # Create graphviz root container
  dot = graphviz.Digraph()
  names = [] # These are the locations we have added to the graph
  # Iterate through all the arcs in the world map
  for arc in world_map:
    # Make a node for the source of the arc
    if arc[0] not in names:
      dot.node(name=str(arc[0]), label=obs_location(world_map_observations[arc[0]]))
      names.append(arc[0])
    # Make a node for the target of the arc
    if arc[2] not in names:
      dot.node(name=str(arc[2]), label=obs_location(world_map_observations[arc[2]]))
      names.append(arc[2])
    # Make an edge
    dot.edge(str(arc[0]), str(arc[2]), label=arc[1].split(' ')[1])
  # Render to file
  dot.render(filename + '.gv', view=False)
  (graph,) = pydot.graph_from_dot_file(filename + '.gv')
  graph.write_png(filename + '.png')
  return Image(filename + '.png')

Reset the game, reset graph and hash_table

In [21]:
WORLD_MAP, WORLD_MAP_OBSERVATIONS, COORDINATES = mapper(ENV)
render_map(WORLD_MAP, WORLD_MAP_OBSERVATIONS)

close door: close door to west
close door: close door to south
state: kitchen -- depth: 0
actions: ['move west', 'move south']
try move west
close door: close door to east
open door: open door to east
state: pantry -- depth: 1
actions: ['move east']
base case
return to previous
close door: close door to south
close door: close door to west
open door: open door to south
open door: open door to west
now at kitchen
try move south
close door: close door to north
close door: close door to east
open door: open door to east
open door: open door to north
state: backyard -- depth: 1
actions: ['move north', 'move east']
try move north
nope, don't return to parent
try move east
close door: close door to north
close door: close door to west
open door: open door to north
open door: open door to west
state: corridor -- depth: 2
actions: ['move west', 'move north']
try move west
nope, don't return to parent
try move north
close door: close door to south
open door: open door to south
state: bedroom --

ExecutableNotFound: failed to execute WindowsPath('dot'), make sure the Graphviz executables are on your systems' PATH

# Build State Space

**TODO: move this code somewhere where the students cannot see it**

**Now using the mapper to identify all rooms and get the default (all doors closed) observation of each room.**

**TODO: inventory tracking MAYBE working properly**


Some helper functions

In [ ]:
### Do the action for astar
def do_action_astar(action, env):
  # Execute the action
  obs, reward, done, infos = env.step(action)
  # Execute the look action to get observation text
  obs, reward, done, infos = env.step('look around')
  # Make the modified observation with inventory added
  modified_obs = obs_with_inventory(obs, env)
  # Get the valid actions, except for inventory and look
  valid_actions = infos['validActions']
  valid_actions.remove('inventory')
  valid_actions.remove('look around')
  return State(id=obs_to_id(modified_obs), observation=modified_obs), valid_actions

### Given a list of actions, execute each of them
def move_along_path(path, env):
  current_state = None # Current state
  # execute each action in the path
  for act in path:
    current_state, _ = do_action_astar(act, env)
  return current_state

### Reset environment for astar
def reset_astar(env):
  # Reset environment
  obs, infos = env.reset(seed=SEED, gameFold="train", generateGoldPath=True)
  # Get modified observation text with inventory included
  modified_obs = obs_with_inventory(obs, env)
  # Get the valid actions, except for inventory and look
  valids = infos['validActions']
  valids.remove('inventory')
  valids.remove('look around')
  return State(id=obs_to_id(modified_obs), observation=modified_obs), valids

### Make a simple version of observation text
### Includes: location, inventory, and status of doors
def simplify_observation(obs):
  open_doors = re.findall(r'open[a-z\- ]*door', obs)
  closed_doors = re.findall(r'closed[a-z\- ]*door', obs)
  return obs_location(obs) + '\ninv: ' + obs_inventory(obs) + '\n' + ', '.join(open_doors +  closed_doors)


The function to walk the state space and build a graph. The walk is pretty simple. It exhaustively maps the unique states. Each time it finds a new state, it resets to the initial state and walks to a state and sees if it can find another state.

The result is a graph, which is a list of tuples of the form `(id1, id2, action_string)`

It also generates a hash_table with which one can retrieve the state description text from a state identifier.

In [ ]:
def obs_things(obs):
  things1 = re.findall(r'[yY]ou \w*\s*see a ([a-zA-Z0-9\- ]+)\,? that ([a-zA-Z0-9\- ]+).', obs)
  things2 = re.findall(r'[tT]here is \w*\s*([a-zA-Z0-9\- ]+)\,? that ([a-zA-Z0-9\- ]+).', obs)
  things3 = re.findall(r'[tT]here is \w*\s*([a-zA-Z0-9\- ]+).', obs)
  things3 = list(filter(lambda s:'that' not in s, things3))
  return things1 + things2 + things3

def parse_doors(obs):
  open_doors = re.findall(r'open[a-z\- ]*door', obs)
  open_doors = list(map(lambda s: (' '.join(s.split(' ')[1:]), 'open'), open_doors))
  closed_doors = re.findall(r'closed[a-z\- ]*door', obs)
  closed_doors = list(map(lambda s: (' '.join(s.split(' ')[1:]), 'closed'), closed_doors))
  doors = sorted(open_doors + closed_doors, key=lambda x:x[0])
  return doors

def parse_room(obs):
  # open_doors = re.findall(r'open[a-z\- ]*door', obs)
  # open_doors = list(map(lambda s: (' '.join(s.split(' ')[1:]), 'open'), open_doors))
  # closed_doors = re.findall(r'closed[a-z\- ]*door', obs)
  # closed_doors = list(map(lambda s: (' '.join(s.split(' ')[1:]), 'closed'), closed_doors))
  # doors = sorted(open_doors + closed_doors, key=lambda x:x[0])
  # location = obs_location(obs)
  things = sorted(obs_things(obs), key=lambda x: x[0] if type(x) is tuple else x)
  return {'things': things}
  # return Room(location, open_doors + closed_doors, things)

def make_world_state(obs, world_map_hash_table, rooms):
  world_state = {'location': obs_location(obs), 'inventory': obs_inventory(obs), 'rooms': {}, 'doors': {}}
  all_doors = []
  rooms_hash = {}
  for room in sorted(rooms):
    room_obs = world_map_hash_table[room]
    rooms_hash[room] = parse_room(room_obs)
    world_state['rooms'] = rooms_hash
    all_doors = list(set(all_doors + parse_doors(room_obs)))
  for door, status in sorted(all_doors, key=lambda x:x[0]):
    world_state['doors'][door] = status
  return world_state

def update_world_state(world_state, obs):
  location = obs_location(obs)
  inventory = obs_inventory(obs)
  new_world_state = copy.deepcopy(world_state)
  new_world_state['location'] = location
  new_world_state['inventory'] = inventory
  new_world_state['rooms'][location] = parse_room(obs)
  doors = parse_doors(obs)
  for door, status in doors:
    new_world_state['doors'][door] = status
  return new_world_state

def hash_world_state(world_state):
  return hash(json.dumps(world_state))

def list_to_pretty_string(lst, indent=0):
  out = ''
  indent_str = ' '*indent
  for item in lst:
    out = out + indent_str + '- ' + str(item) + '\n'
  return out

def dict_to_pretty_string(d, indent = 0, no_keys = []):
  out = ''
  indent_str = ' '*indent
  for n, key in enumerate(d):
    if key not in no_keys:
      value = d[key]
      out = out + indent_str + key + ': '
      if type(value) is dict:
        out = out + '\n' + dict_to_pretty_string(value, indent = indent+1, no_keys = no_keys)
      elif type(value) is list:
        out = out + '\n' + list_to_pretty_string(value, indent = indent+1)
      else:
        end = '\n' if n < len(d)-1 else ''
        out = out + str(value) + end
  return out

def world_state_to_string(world_state, no_keys = ['rooms']):
  out = dict_to_pretty_string(world_state, no_keys = no_keys)
  return out

In [ ]:
def generate_state_space(env, world_map, world_map_observations):
  init_state, valids = reset_astar(env)
  init_state_observation = init_state.observation
  rooms = list(set(list(map(lambda arc: arc[0], world_map)) + list(map(lambda arc:arc[2], world_map))))
  init_world_state = make_world_state(init_state.observation, world_map_observations, rooms)
  init_world_state = update_world_state(init_world_state, init_state.observation)
  init_state_id = hash_world_state(init_world_state)
  queue = [(init_state_id, a) for a in valids]
  world_state_hash = {init_state_id: init_world_state}
  world_state_parents = {init_state_id: None}
  world_obs_hash = {init_state_id: init_state_observation}
  graph = []
  while len(queue) > 0:
    current_id, act = queue.pop(0)
    current_state = world_state_hash[current_id]
    print("\ncurrent:", current_id)
    print(world_state_to_string(current_state))
    # Move to current state
    temp_state, _ = reset_astar(env)
    path = []
    cur = current_id
    while world_state_parents[cur] is not None:
      cur, a = world_state_parents[cur]
      path.append(a)
    path = reversed(path)
    for a in path:
      temp_state, _ = do_action_astar(a, env)
    print("do act:", act)
    new_state, valids = do_action_astar(act, env)
    new_state_observation = new_state.observation
    new_state = update_world_state(current_state, new_state.observation)
    new_state_id = hash_world_state(new_state)
    world_state_hash[new_state_id] = new_state
    world_obs_hash[new_state_id] = new_state_observation
    print("\nnew state:", new_state_id)
    print(world_state_to_string(new_state))
    print("valids:", valids)
    graph.append((current_id, new_state_id, act))
    if new_state_id not in world_state_parents:
      world_state_parents[new_state_id] = (current_id, act)
      for a in valids:
        if (new_state_id, a) not in queue:
          queue.append((new_state_id, a))
    print('queue:', len(queue))
  return graph, world_state_hash, world_obs_hash

In [ ]:
GRAPH, WORLD_STATE_HASH, WORLD_OBSERVATION_HASH = generate_state_space(ENV, WORLD_MAP, WORLD_MAP_OBSERVATIONS)

Streaming output truncated to the last 5000 lines.
valids: ['move east', 'close door to east', 'open door to north', 'open door to east', 'move north', 'close door to north']
queue: 121

current: 1274802410432305455
location: backyard
inventory: a coin
doors: 
 frosted-glass door: open
 screen door: open
 sliding patio door: closed
 wood door: open
do act: close door to north

new state: 1274802410432305455
location: backyard
inventory: a coin
doors: 
 frosted-glass door: open
 screen door: open
 sliding patio door: closed
 wood door: open
valids: ['move east', 'close door to east', 'open door to north', 'open door to east', 'move north', 'close door to north']
queue: 120

current: -6299267549759308834
location: corridor
inventory: a coin
doors: 
 frosted-glass door: open
 screen door: closed
 sliding patio door: closed
 wood door: open
do act: move west

new state: -6299267549759308834
location: corridor
inventory: a coin
doors: 
 frosted-glass door: open
 screen door: closed
 sliding

Render the state space graphically. Right now we assume that a state can be uniquely described by the room location and the inventory. This is probably only true for coin worlds.

In [ ]:
def render_state_space(graph, world_state_hash, filename = 'space'):
  # Create graphviz root container
  dot = graphviz.Digraph()
  nodes = []
  edges = []
  for arc in graph:
    parent, child, act = arc
    parent_name = str(abs(parent))
    child_name = str(abs(child))
    if child not in nodes:
      dot.node(name=child_name, label=world_state_to_string(world_state_hash[child]))
      nodes.append(child)
    if parent not in nodes:
      dot.node(name=parent_name, label=world_state_to_string(world_state_hash[parent]))
      nodes.append(parent)
    if (parent, child, act) not in edges:
      dot.edge(parent_name, child_name, label=act)
      edges.append((parent, child, act))
  # Render to file
  dot.render(filename + '.gv', view=False)
  (graph,) = pydot.graph_from_dot_file(filename + '.gv')
  graph.write_png(filename + '.png')
  return Image(filename + '.png')

In [ ]:
render_state_space(GRAPH, WORLD_STATE_HASH)

**TODO: Store state spaces along with seeds in a file**

# Breadth-First Search (BFS)

**TODO: the state space graph representation has changed. The world state representation has changed. The world state hash table has changed.**

The states are unique ids for each state.

The state space consists of `(state_id1, state_id2, action_string)` tuples.

For debugging purposes it is helpful to render text from ids using the `hash_table`.

The goal is achieved if the coin is in the inventory.

In [ ]:
def is_goal(the_state):
  return 'coin' in the_state['inventory']

Successors returns a list of tuples of the form `(state_id, generating_action)`.

In [ ]:
def get_successors(state, graph):
  successors = []
  for arc in graph:
    if arc[0] == state:
      successors.append((arc[1], arc[2]))
  return successors

Initialize the world

In [ ]:
def init_state_for_astar(env, world_map, world_map_observations):
  init_state, _ = reset_astar(env)
  rooms = list(set(list(map(lambda arc: arc[0], world_map)) + list(map(lambda arc:arc[2], world_map))))
  init_world_state = make_world_state(init_state.observation, world_map_observations, rooms)
  init_state_id = hash_world_state(init_world_state)
  return init_state_id

In [ ]:
init_state = init_state_for_astar(ENV, WORLD_MAP, WORLD_MAP_OBSERVATIONS)
print(init_state)
print(world_state_to_string(WORLD_STATE_HASH[init_state]))

-5164763243569538204
location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: closed
 wood door: closed


In [ ]:
def bfs(init_state, graph, world_state_hash):
  open = [init_state]
  closed = set()
  current = init_state
  parents = {init_state: None}
  plan = []
  count = 0
  while not is_goal(world_state_hash[current]) and len(open) > 0:
    current = open.pop(0)
    print('current:\n', world_state_to_string(world_state_hash[current]))
    closed.add(current)
    successors = get_successors(current, graph)
    for s_id, a in successors:
      if s_id not in closed:
        parents[s_id] = (current, a)
        open.append(s_id)
    print("queue:", len(open))
    count = count + 1
  if is_goal(world_state_hash[current]):
    cur = current
    while parents[cur] is not None:
      cur, act = parents[cur]
      plan.append(act)
    plan = list(reversed(plan))
    print("iters", count)
  return plan

In [ ]:
plan = bfs(init_state, GRAPH, WORLD_STATE_HASH)
print(plan)

current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: closed
 wood door: closed
queue: 2
current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 3
current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: open
 screen door: closed
 sliding patio door: closed
 wood door: closed
queue: 4
current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: open
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 5
current:
 location: backyard
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 6
current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: open
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 7
current:
 location: pantry
inventory: empty
doors: 
 frosted-glas

# A*

Get the (x, y) position of the goal state. Do this by "running" the goal action sequence.

In [ ]:
def get_goal_coordinates(ENV):
  # Get the gold solution
  gold = ENV.getGoldActionSequence()
  # Start in (0, 0)
  coordinates = (0, 0)
  # Run the gold solution
  for act in gold:
    coordinates = change_coordinates(coordinates, act)
  return coordinates

**Part of solution** I don't know how to do a good insert sort with python so I wrote my own

In [ ]:
def insert_sort(new_item, the_list, criterion_fn = lambda x: x):
  for i, item in enumerate(the_list):
    if criterion_fn(new_item) < criterion_fn(item):
      break
  return the_list[:i] + [new_item] + the_list[i:]



Heuristic will be Euclidean distance between current state coordinates and goal state coordinates.

In [ ]:
def distance(coords1, coords2):
  return math.sqrt((coords1[0] - coords2[0])**2 + (coords1[1] - coords2[1])**2)

def h(state, goal_coordinates):
  return distance(COORDINATES[WORLD_STATE_HASH[state]['location']], goal_coordinates)

**A* solution**

In [ ]:
def a_star(init_state, graph, world_state_hash, goal_coordinates):
  open = [init_state]
  closed = set()
  current = init_state
  parents = {init_state: None}
  plan = []
  count = 0
  while not is_goal(world_state_hash[current]) and len(open) > 0:
    current = open.pop(0)
    print('current:\n', world_state_to_string(world_state_hash[current]))
    closed.add(current)
    successors = get_successors(current, graph)
    for s_id, a in successors:
      if s_id not in closed:
        parents[s_id] = (current, a)
        open.append(s_id)
        open = insert_sort(s_id, open, criterion_fn = lambda x: h(x, goal_coordinates))
    print("queue:", len(open))
    count = count + 1
  if is_goal(world_state_hash[current]):
    cur = current
    while parents[cur] is not None:
      cur, act = parents[cur]
      plan.append(act)
    plan = list(reversed(plan))
    print("iters", count)
  return plan

Set up the initial state, also get the goal's coordinates for the heuristic.

In [ ]:
init_state = init_state_for_astar(ENV, WORLD_MAP, WORLD_MAP_OBSERVATIONS)
print(init_state)
print(world_state_to_string(WORLD_STATE_HASH[init_state]))
GOAL_COORDINATES = get_goal_coordinates(ENV)

-5164763243569538204
location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: closed
 wood door: closed


Run A*

In [ ]:
plan = a_star(init_state, GRAPH, WORLD_STATE_HASH, GOAL_COORDINATES)
print(plan)

current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: closed
 wood door: closed
queue: 4
current:
 location: kitchen
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 7
current:
 location: backyard
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: closed
 sliding patio door: open
 wood door: closed
queue: 10
current:
 location: backyard
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: open
 sliding patio door: open
 wood door: closed
queue: 15
current:
 location: corridor
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: open
 sliding patio door: open
 wood door: closed
queue: 20
current:
 location: corridor
inventory: empty
doors: 
 frosted-glass door: closed
 screen door: open
 sliding patio door: open
 wood door: open
queue: 27
current:
 location: corridor
inventory: empty
doors: 
 frosted

# Tabular RL

In [ ]:
def reset_mdp(env):
  obs, infos = env.reset(seed=SEED, gameFold="train", generateGoldPath=True)
  valids = infos['validActions']
  valids.remove('inventory')
  valids.remove('look around')
  return obs, valids

def make_state_mdp(obs, env):
  modified_obs = obs_with_inventory(obs, env)
  return State(id=obs_to_id(modified_obs), observation=modified_obs)

def do_action_mdp(action, env):
  obs_step, reward_step, done_step, infos_step = env.step(action)
  obs_look, reward_look, done_look, infos_look = env.step('look around')
  valid_actions = infos_step['validActions']
  valid_actions.remove('inventory')
  valid_actions.remove('look around')
  return obs_look, reward_step, done_step, valid_actions

def state_max(q_table, state):
  best_value = -float('inf')
  for i, a in enumerate(q_table[state.id]):
    value = q_table[state.id][a]
    if value > best_value:
      best_value = value
  return best_value

def state_argmax(q_table, state):
  best_action = None
  best_value = -float('inf')
  for i, a in enumerate(q_table[state.id]):
    value = q_table[state.id][a]
    if value > best_value:
      best_value = value
      best_action = a
  return best_action


In [ ]:
EPISODES = 100
THRESHOLD = 25
LR = 0.5
GAMMA = 0.5

In [ ]:
def q_learning(env, episodes = 100, threshold = 25, lr = 0.5, gamma = 0.5):
  # Set up q-table
  q_table = {}
  mdp_observations_map = {}
  episode_rewards = [0.0]
  # Run episodes
  for n in range(episodes):
    print("episode:", n)
    total_reward = 0.0
    t = 0 # time step
    done = False # terminal state?
    # Reset environment and get first observation
    obs, valid_actions = reset_mdp(env)
    state = make_state_mdp(obs, env)
    mdp_observations_map[state.id] = state.observation
    # run a game
    while not done and t < threshold:
      # Make sure we have set up the q-table row
      if state.id not in q_table:
        q_table[state.id] = {}
        for a in valid_actions:
          q_table[state.id][a] = 0.0
      # pick a random action
      action = random.choice(valid_actions)
      # Run the action
      new_obs, reward, done, new_valid_actions = do_action_mdp(action, env)
      new_state = make_state_mdp(new_obs, env)
      mdp_observations_map[new_state.id] = new_state.observation
      # make sure we have set up the q-table row for new state
      if new_state.id not in q_table:
        q_table[new_state.id] = {}
        for a in new_valid_actions:
          q_table[new_state.id][a] = 0.0
      # Bellman update
      if not done:
        Q_sa = q_table[state.id][action]
        Q_sprime_aprime = state_max(q_table, new_state)
        new_Q_sa = Q_sa + (lr * (reward + (gamma * Q_sprime_aprime) - Q_sa))
        q_table[state.id][action] = new_Q_sa
      else:
        Q_sa = q_table[state.id][action]
        Q_sprime_aprime = state_max(q_table, new_state)
        new_Q_sa = Q_sa + (lr * (reward - Q_sa))
        q_table[state.id][action] = new_Q_sa
      # increment counter
      t = t + 1
      # increment total reward
      total_reward = total_reward + reward
      # prepare for next game iteration
      obs = new_obs
      state = new_state
      valid_actions = new_valid_actions
    print("total reward:", total_reward, "steps:", t)
  return q_table, mdp_observations_map

In [ ]:
q_table, mdp_observations_map = q_learning(ENV,
                                           episodes = EPISODES,
                                           threshold = THRESHOLD,
                                           lr = LR,
                                           gamma = GAMMA)

episode: 0
total reward: 0.0 steps: 25
episode: 1
total reward: 0.0 steps: 25
episode: 2
total reward: 0.0 steps: 25
episode: 3
total reward: 0.0 steps: 25
episode: 4
total reward: 0.0 steps: 25
episode: 5
total reward: 0.0 steps: 25
episode: 6
total reward: 0.0 steps: 25
episode: 7
total reward: 0.0 steps: 25
episode: 8
total reward: 0.0 steps: 25
episode: 9
total reward: 0.0 steps: 25
episode: 10
total reward: 0.0 steps: 25
episode: 11
total reward: 0.0 steps: 25
episode: 12
total reward: 0.0 steps: 25
episode: 13
total reward: 0.0 steps: 25
episode: 14
total reward: 0.0 steps: 25
episode: 15
total reward: 0.0 steps: 25
episode: 16
total reward: 0.0 steps: 25
episode: 17
total reward: 0.0 steps: 25
episode: 18
total reward: 0.0 steps: 25
episode: 19
total reward: 0.0 steps: 25
episode: 20
total reward: 1.0 steps: 24
episode: 21
total reward: 0.0 steps: 25
episode: 22
total reward: 0.0 steps: 25
episode: 23
total reward: 0.0 steps: 25
episode: 24
total reward: 0.0 steps: 25
episode: 2

In [ ]:
for k in q_table:
  obs = mdp_observations_map[k]
  print(k, q_table[k])
  print(simplify_observation(obs))


6344817019421266524 {'close door to west': 0.033924303309357334, 'move west': 0.033751328335466846, 'open door to south': 0.06460922991216828, 'open door to west': 0.028246528746490907, 'move south': 0.03345050459597303, 'close door to south': 0.035609417430944035}
kitchen
inv: empty
closed sliding patio door, closed frosted-glass door
9184828748396534073 {'close door to west': 0.0744495861030557, 'open door to south': 0.0657636937487493, 'open door to west': 0.05716508579856805, 'close door to south': 0.03241640861554519, 'move west': 0.06419226112580415, 'move south': 0.12749126306886893}
kitchen
inv: empty
open sliding patio door, closed frosted-glass door
7423446085023893555 {'move west': 0.02044666651467947, 'open door to west': 0.056496325274565606, 'close door to south': 0.028189457830279707, 'move south': 0.11462868744274601, 'close door to west': 0.061966448671943564, 'open door to south': 0.05697044892621861}
kitchen
inv: empty
open sliding patio door, open frosted-glass door

In [ ]:
def run_policy(q_table, env, threshold = 25):
  t = 0
  done = False
  actions = []
  # Reset environment and get first observation
  obs, valid_actions = reset_mdp(env)
  state = make_state_mdp(obs, env)
  # run a game
  while not done and t < threshold:
    action = state_argmax(q_table, state)
    actions.append(action)
    new_obs, reward, done, new_valid_actions = do_action_mdp(action, env)
    new_state = make_state_mdp(new_obs, env)
    print(new_state)
    obs = new_obs
    state = new_state
    t = t + 1
  return actions

In [ ]:
plan = run_policy(q_table, ENV, threshold = THRESHOLD)
print(plan)

State(id=9184828748396534073, observation='You are in the kitchen. In one part of the room you see a stove. There is also an oven. You also see a fridge that is closed. In another part of the room you see a counter, that has nothing on it. In one part of the room you see a kitchen cupboard that is closed. There is also a cutlery drawer that is closed. You also see a trash can that is closed. In another part of the room you see a dishwasher that is closed. In one part of the room you see a dining chair, that has nothing on it. \nThrough an open sliding patio door, to the South you see the backyard. To the West you see a closed frosted-glass door. \nInventory (maximum capacity is 2 items): \n  Your inventory is currently empty.\n')
State(id=3571910332989166514, observation='You are in the backyard. In one part of the room you see a barbeque. There is also a workbench, that has nothing on it. You also see a patio chair, that has nothing on it. In another part of the room you see a patio t

# **DQN**

Load pytorch

In [ ]:
import torch
from torch import nn
import torch.nn.functional as F
import torch.optim as optim

Note whether we will be working on the GPU (`cuda`) or CPU (`cpu`).

In [ ]:
DEVICE = 'cuda' if torch.cuda.is_available() else 'cpu'
print(DEVICE)

cpu


We need to know the vocabulary of the game. This is all the words that will ever be used. We create a special object that keeps track of the words and also can convert words to tokens. A token is a number that uniquely identifies a word.

In [ ]:
EOS_token = 0    # A special token representing the end of a sequence
SOS_token = 1    # A special token representing the end of a sequence

class Vocab:
    def __init__(self, name):
        self.name = name                             # The name of the vocabulary
        self._word2index = {'EOS': 0, 'SOS': 1}      # Map words to token index
        self._word2count = {'EOS': 0, 'SOS': 0}      # Track how many times a word occurs in a corpus
        self._index2word = {0: "EOS", 1: "SOS"}      # Map token indexs back into words
        self._n_words = 2 # Count SOS and EOS        # Number of unique words in the corpus

    # Get a list of all words
    def get_words(self):
      return list(self._word2count.keys())

    # Get the number of words
    def num_words(self):
      return self._n_words

    # Convert a word into a token index
    def word2index(self, word):
      return self._word2index[word]

    # Convert a token into a word
    def index2word(self, word):
      return self._index2word[word]

    # Get the number of times a word occurs
    def word2count(self, word):
      return self._word2count[word]

    # Add all the words in a sentence to the vocabulary
    def add_sentence(self, sentence):
        for word in sentence.split(' '):
            self.add_word(word)

    # Add a single word to the vocabulary
    def add_word(self, word):
        if word not in self._word2index:
            self._word2index[word] = self._n_words
            self._word2count[word] = 1
            self._index2word[self._n_words] = word
            self._n_words += 1
        else:
            self._word2count[word] += 1

Helper functions for making a vocabulary

In [ ]:
### Separate punctuation into separate tokens
### Remove anything that is not a letter, number, or punctuation
def normalize_string(s):
    s = s.lower().strip()
    s = re.sub(r"([.!?])", r" \1", s)
    s = re.sub(r"[^a-zA-Z0-9.!?]+", r" ", s)
    return s

### Pass in observations from the game, record each unique word
def make_vocab(observations, vocab_name = ''):
  vocab = Vocab(vocab_name)
  for obs in observations:
    words = normalize_string(obs).split()
    for w in words:
      vocab.add_word(w)
  return vocab

Create the vocabular from all the observations we have collected from the game

In [ ]:
VOCAB = make_vocab(WORLD_OBSERVATION_HASH.values())
print('vocab size:', VOCAB.num_words())

vocab size: 89


We also need to be able to translate actions to numbers and back again

In [ ]:
def action_vocab():
  actions = []
  for d in ['north', 'south', 'east', 'west']:
    actions.append('move ' + d)
    actions.append('open door to ' + d)
  return actions + ['take coin']

In [ ]:
ACTIONS = action_vocab()
print('action vocab:', ACTIONS)
print('action vocab size:', len(ACTIONS))

action vocab: ['move north', 'open door to north', 'move south', 'open door to south', 'move east', 'open door to east', 'move west', 'open door to west', 'take coin']
action vocab size: 9


Create a special data structure for game state transitions consisting of:
- State
- Action
- Next state
- Reward

These will be used in the replay memory.

Named tuples allows one to access each slot in the data structure by it's name, e.g.:
```
t = Transition(state='start', action=2, next_state='end', reward=0.0)
print(t.action)
>> 2
```

In [ ]:
Transition = namedtuple('Transition',
                        ('state', 'action', 'next_state', 'reward'))

If you want to do replay memory weighted prioritization, you can use this function. It takes in a list of elements, along with a list of weights for the elements, and returns *k* elements.

In [ ]:
def weighted_sample_without_replacement(elements, weights, k):
  v = [random.random() ** (1 / w) for w in weights]
  order = sorted(range(len(elements)), key=lambda i: v[i])
  return [elements[i] for i in order[-k:]]

Replay Memory object implements a ring buffer
- capacity: number of elements the memory is allowed to hold
- memory: a list of Transition objects
- position: the position in the ring buffer that will be written to next time an element is pushed.
- weights (optional): the weight corresponding to each element in memory. Set all weights to 1 if not using priority replay.

The following member functions are implemented:
- push (state, action, next_state, reward, weight=1): push a new Transition. Use weight=1 if not using priority replay.
- sample (batch_size): returns the given number of Transition objects as a list

You can retrieve the length of the replay buffer using `len()`, e.g.:
```
buffer = ReplayMemory(100):
len(buffer)
```

In [ ]:
class ReplayMemory(object):

    def __init__(self, capacity):
      self.capacity = capacity
      self.memory = []
      self.position = 0
      self.weights = []

    ### Store a transition in memory.
    ### To implement: put new items at the end of the memory array, unless capacity is reached.
    ###    Combine the arguments into a new Transition object.
    ###    If capacity is reached, start overwriting the beginning of the array.
    ###    Use the position index to keep track of where to put the next item.
    def push(self, state, action, next_state, reward, weight = 1):
      if len(self.memory) < self.capacity:
        self.memory.append(None)
        self.weights.append(None)
      self.memory[self.position] = Transition(state, action, next_state, reward)
      self.weights[self.position] = weight
      self.position = (self.position + 1) % self.capacity

    ### Return a batch of transition objects from memory containing batch_size elements.
    def sample(self, batch_size):
      # return random.sample(self.memory, batch_size)
      return weighted_sample_without_replacement(self.memory, self.weights, batch_size)

    ### This allows one to call len() on a ReplayMemory object. E.g. len(replay_memory)
    def __len__(self):
      return len(self.memory)


The Deep Q-Network neural network object. **solution**

In [ ]:
class DQN(nn.Module):

    ### Create all the nodes in the computation graph.
    ### We won't say how to put the nodes together into a computation graph. That is done
    ### automatically when forward() is called.
    def __init__(self, vocab_size, num_actions):
        super(DQN, self).__init__()
        self.num_actions = num_actions
        self.vocab_size = vocab_size
        self.embed = nn.Embedding(vocab_size, 128)
        self.gru = nn.GRU(128, 128, num_layers=1, batch_first=True)
        self.relu1 = nn.LeakyReLU()
        self.linear1 = nn.Linear(128, 64)
        self.relu2 = nn.LeakyReLU()
        self.linear2 = nn.Linear(64, num_actions)

    # Called with either one element to determine next action, or a batch
    # during optimization. Returns tensor([[left0exp,right0exp]...]).
    def forward(self, x):
      h1 = self.embed(x)
      h2 = self.gru(h1)[1][-1]
      h3 = self.relu1(h2)
      h4 = self.linear1(h3)
      h5 = self.relu2(h4)
      head = self.linear2(h5)
      return head

In [ ]:
def reset_dqn(env):
  obs, infos = env.reset(seed=SEED, gameFold="train")
  final_obs = obs_with_inventory(obs, env)
  return final_obs

Code for executing an action for the DQN. Returns the text of the observation plus inventory.

Checks to see if the action could not be executed by the game engine, and issues a negative reward for that.

Current version (for debugging) also provides a shaped reward, giving partial rewards as the agent moves through the map to the coin. This is hard-coded for the particular seed, and should be re-written in a more general form. Ideally, the agent does not need any shaped reward at all, but we shall see.



In [ ]:
def do_action_dqn(action, env):
  # Execute the action in the environment
  act_obs, act_reward, act_done, act_infos = env.step(action)
  look_obs = act_infos['look'] + '\n' + act_infos['inventory']
  location = obs_location(look_obs)
  inventory = obs_inventory(look_obs)
  if not act_done and 'Unknown' in act_obs or "You can't" in act_obs:
    # Issue negative reward for non-executable actions
    act_reward = -10.0
  elif location == 'corridor' and 'coin' in inventory:
    # Issue higher reward for the coin
    print("---found goal---")
    act_reward = 20.0
    act_done = True
  elif location == 'corridor':
    # Shaped reward for being close to the goal
    act_reward = 10.0
  elif location == 'backyard':
    # Shaped reward for being halfway
    act_reward = 2.5
  else:
    # Everything else results in zero reward
    act_reward = 0.0
  #act_reward = act_reward + (10 - 2 * distance(COORDINATES[obs_location(look_obs)], COORDINATES['corridor']))#GOAL_COORDINATES)
  # Generate final observation with inventory
  #final_obs = obs_with_inventory(look_obs, env)
  return look_obs, act_reward, act_done, act_infos

Convert a state (observation) to tokens. **Possibly something we want students to do**

In [ ]:
# Note: this will not truncate if state tokens exceeds max length
def state2tokens(state, vocab, env, max_len=170):
  s = normalize_string(obs_with_inventory(state, env)).split()
  t = torch.tensor([vocab.word2index(w) for w in s])
  z = torch.zeros(max_len)
  z[0:len(s)] = t
  return z.long().unsqueeze(dim=0)

This smooths a list of numbers (for plotting nicer plots)

In [ ]:
def smooth(sequence, smoothing=3):
  new_seq = []
  for idx in range(len(sequence)):
    subseq = sequence[max(0, idx-smoothing+1):idx+1]
    new_seq.append(sum(subseq) / len(subseq))
  return new_seq

hyperparameters
- BUFFER: the size of the replay memory
- BATCH_SIZE: size of the batch to train on
- THRESHOLD: max length of a trial
- GAMMA: [0, 1] discount factor
- EPSILON: [0, 1] epsilon greedy randomness during training
- EVAL_EPSILON: [0, 1] epsilon greedy randomness during evaluation
- TARGET_UPDATE: how often to update the target network
- NUM_EVALS: number of evaluation per trial during training

In [ ]:
BUFFER = 1000
BATCH_SIZE = 32
THRESHOLD = 25
GAMMA = 0.5
EPSILON = 0.9
EVAL_EPSILON = 0.2
MAX_STEPS = 50000
TARGET_UPDATE = 2
NUM_EVALS = 10

Evaluate the DQN model.

Takes the following parameters:
- model: the DQN model to evaluate
- env: the environment
- vocab: the vocabulary object
- actions: the list of actions
- threshold: the max length of a trial
- epsilon: [0, 1] probability of choosing a random action during execution
- verbose: print out observations and actions if `True`

Returns:
- total reward
- average step reward
- max reward received in any time step
- reward of the final step
- number of steps

In [ ]:
def evaluate(model, env, vocab, actions, threshold, epsilon, verbose = True):
  # Reset the game engine
  state = reset_dqn(env)
  if verbose:
    print(state)
  # Convert state observation to tokens
  state = state2tokens(state, vocab, env).to(DEVICE)
  t = 0 # The time step
  done = False # Are we done?
  total_reward = 0 # total reward accumulated during run
  max_reward = -float('inf') # highest reward we see during run
  # Loop until done or threshold steps met
  while not done and t < threshold:
    # Epsilon greedy
    if random.random() < epsilon:
      # Use random action
      action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
    else:
      # Use the model
      action = model(state).argmax().view(1, 1)
    if verbose:
      print("action", actions[action.item()])
    # execute the action
    next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
    if verbose:
      print(reward)
      print(next_state)
    # record stats
    total_reward = total_reward + reward
    max_reward = max(max_reward, reward)
    next_state = state2tokens(next_state, vocab, env).to(DEVICE)
    # update current state
    state = next_state
    # increment time step
    t = t + 1
  if verbose:
    print("total", total_reward)
  return total_reward, total_reward / t, max_reward, reward, t

Populate the replay memory with random transitions. This is done by running a 100% random agent. **Possibly something we want students to do**

In [ ]:
def populate_replay_memory(replay_memory, env, vocab, actions):
  steps = 0 # total number of steps executed
  # Continue until the buffer is full
  while steps < replay_memory.capacity:
    # Reset the environment
    state = reset_dqn(env)
    # Convert state observation to tokens
    state = state2tokens(state, vocab, env).to(DEVICE)
    done = False # Are we done with a trial?
    t = 0 # number of steps in trial
    # Run one trial
    while not done and t < THRESHOLD:
      # Get a random action
      action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
      # increment total steps
      steps = steps + 1
      # increment trial steps
      t = t + 1
      # Execute the action
      next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
      next_state = state2tokens(next_state, vocab, env).to(DEVICE)
      reward = torch.tensor([[reward]], device=DEVICE)
      # Push transition information to replay memory
      replay_memory.push(state, action, next_state if not done else None, reward)
      # Get ready for next trial iteration
      state = next_state

Train the agent. Returns the model as of the last iteration, and also the best version of the model seen during training. **Students should do some or all of this. In other classes I have them do the part where they make the batches and run the neural net, compute loss, and call backprop. I can also see value in implementing the trial execution code. Very similar to populate() above.**

In [ ]:
def train(env, vocab, actions, epsilon, threshold,
          max_steps, buffer_size, batch_size, gamma, eval_epsilon,
          target_update = 2, num_evals = 10, smoothing = 3):
  steps = 0 # total number of training steps
  current_epsilon = epsilon
  # Create the model
  model = DQN(vocab_size = vocab.num_words(), num_actions = len(actions))
  model.to(DEVICE)
  model.train()
  # initialize the optimizer
  #optimizer = optim.SGD(model.parameters(), lr=0.001)
  optimizer = optim.RMSprop(model.parameters())
  # Initialize target network
  target = DQN(vocab_size = vocab.num_words(), num_actions = len(actions))
  target.load_state_dict(model.state_dict())
  target.to(DEVICE)
  # This keeps the best version of the model we've seen so far
  best = DQN(vocab_size = vocab.num_words(), num_actions = len(actions))
  best.load_state_dict(model.state_dict())
  best.to(DEVICE)
  best.eval()
  # initialize and populate the replay memory
  replay_memory = ReplayMemory(buffer_size)
  populate_replay_memory(replay_memory, env, vocab, actions)
  # Keep track of best evaluation reward
  best_eval_reward = -float('inf')
  trial_num = 0
  # For plotting
  plot_train_x = []
  plot_train_y = []
  plot_eval_x = []
  plot_eval_y = []
  # Loop until max training steps reached
  while steps < max_steps:
    # reset the environment
    state = reset_dqn(env)
    # convert state observation to tokens
    state = state2tokens(state, vocab, env).to(DEVICE)
    done = False # Are we done?
    trial_total_reward = 0.0 # total trial reward
    best_trial_reward = 0.0 # best trial reward
    t = 0 # number of steps in trial
    print('\nTRIAL', trial_num)
    # Run one trial
    while not done and t < threshold:
      # Epsilon greedy
      if random.random() < current_epsilon:
        # Random action
        action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
      else:
        # Use the model to generate an action
        with torch.no_grad():
          action = model(state).argmax().view(1, 1)
      # update epsilon
      current_epsilon = epsilon - (epsilon * (steps / max_steps))
      # increment total training steps
      steps = steps + 1
      # increment trial steps
      t = t + 1
      # execute the action
      next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
      # keep track of stats
      best_trial_reward = max(best_trial_reward, reward)
      trial_total_reward = trial_total_reward + reward
      # convert state observation to tokens
      next_state = state2tokens(next_state, vocab, env).to(DEVICE)
      # Create tensor of reward
      reward = torch.tensor([[reward]], device=DEVICE)
      # Push transition to memory
      replay_memory.push(state, action, next_state if not done else None, reward)
      # update state for next trial iteration
      state = next_state
      # TRAINING:
      # Sample replay memory
      transitions = replay_memory.sample(batch_size)
      # Build a batch
      batch = Transition(*zip(*transitions))
      states_batch = torch.cat(batch.state)
      actions_batch = torch.cat(batch.action)
      rewards_batch = torch.cat(batch.reward)
      # Which transitions are non-terminal?
      non_final_mask = torch.tensor(tuple(map(lambda s: s is not None, batch.next_state)), dtype=torch.bool, device=DEVICE)
      # Next states batch might be smaller than state batch if there are terminal transitions
      next_states_batch = torch.cat([s for s in batch.next_state if s is not None])
      # Get q-values for the actions executed
      state_action_values = model(states_batch).gather(1, actions_batch)
      # Initialize q-values for the next state to all zeros
      next_state_values = torch.zeros(BATCH_SIZE, device=DEVICE)
      # Run the target model on next states and fill in the non-terminal rows
      next_state_values[non_final_mask] = target(next_states_batch).max(dim=1)[0]
      next_state_values = next_state_values.unsqueeze(1)
      # Don't gradient descent through the next state values
      next_state_values.detach()
      # Get the expected values for the next states
      expected_state_action_values = rewards_batch + (next_state_values * gamma)
      # Loss is difference from actual state action values and expected state action values
      loss = F.smooth_l1_loss(state_action_values, expected_state_action_values)
      # Back propagate loss
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()
      # Clip gradients if necessary
      for param in model.parameters():
        param.grad.data.clamp_(-1, 1)
      # Update target model
      if steps % target_update == 0:
        target.load_state_dict(model.state_dict())
      # END OF TRIAL LOOP
    # EVALUATION
    print("total training steps", steps, 'epsilon', current_epsilon)
    print("steps", t,
          "total", trial_total_reward,
          "average", trial_total_reward / t,
          "best", best_trial_reward,
          '\n')
    eval_total_reward = 0.0 # evaluate stats
    # Run evaluation a number of times
    for i in range(10):
      # Call evaluation code
      eval_total_r, eval_avg_r, eval_max_r, eval_final_r, eval_steps = evaluate(model, env, vocab, actions, threshold, epsilon=eval_epsilon, verbose=False)
      print('eval #:', i,
            'steps', eval_steps,
            'total', eval_total_r,
            'avg', eval_avg_r,
            'max', eval_max_r)
      eval_total_reward = eval_total_reward + eval_avg_r
    # Plot eval stats for the training trial and the evaluations
    plot_train_x.append(steps)
    plot_eval_x.append(steps)
    plot_eval_y.append(eval_total_reward / 10)
    plot_train_y.append(trial_total_reward / t)
    plt.plot(plot_train_x, smooth(plot_train_y, smoothing=smoothing), label="train")
    plt.plot(plot_eval_x, smooth(plot_eval_y, smoothing=smoothing), label="eval")
    plt.legend()
    plt.show()
    # increment trial number
    trial_num = trial_num + 1
    # Save the best model
    if (eval_total_reward / t) >= best_eval_reward:
      best_eval_reward = eval_total_reward / t
      best.load_state_dict(model.state_dict())
      print("-----------------NEW BEST-------------------")
  return model, best

Run the training

In [ ]:
last, best = train(ENV, VOCAB, ACTIONS,
                   epsilon = EPSILON,
                   threshold = THRESHOLD,
                   max_steps = MAX_STEPS,
                   buffer_size = BUFFER,
                   batch_size = BATCH_SIZE,
                   gamma = GAMMA,
                   eval_epsilon = EVAL_EPSILON,
                   target_update = TARGET_UPDATE,
                   num_evals = NUM_EVALS)

What do we want to see during training? What are these stats telling us?

We get a report after every trial. We want to see trials receive a positive best reward. Negative reward means it is performing illegal actions. Zero reward means it isn't making any progress toward the goal.

After each trial, we also get a number of evaluation results. We want to see the average reward above 0.0. Negative numbers means it hasn't figured out how not to do illegal actions. If the average is negative then most actions are illegal. We also want to see a positive max reward. Zero max reward means not much progress. If steps are `threshold` length, then the agent is timing out without hitting the goal.

If we see training trials hit max reward, then we know it is finding it's way to the goal. That is good, but it could be because of random actions, especially when epsilon is high. But it also means that transitions to the goal are now in the replay buffer and this means (not right away) that the agent should learn how to make that transition to the goal.

Eventually, we should see training trials hit max reward more often. This is a good sign when epsilon is low. We should also start to see more and more evaluations hit max reward.

Evaluate the best model

In [ ]:
for i in range(NUM_EVALS):
  print('---')
  print('eval #', i)
  total_r, avg_r, max_r, final_r, steps = evaluate(best, ENV, VOCAB, ACTIONS,
                                                   threshold = THRESHOLD,
                                                   epsilon = EVAL_EPSILON,
                                                   verbose = False)
  print('steps', steps,
        'total', total_r,
        'avg', avg_r,
        'max', max_r,
        'final', final_r)

---
eval # 0
---found goal---
steps 7 total 10.0 avg 1.4285714285714286 max 10.0 final 10.0
---
eval # 1
---found goal---
steps 7 total -10.0 avg -1.4285714285714286 max 10.0 final 10.0
---
eval # 2
---found goal---
steps 5 total 10.0 avg 2.0 max 10.0 final 10.0
---
eval # 3
---found goal---
steps 5 total 10.0 avg 2.0 max 10.0 final 10.0
---
eval # 4
---found goal---
steps 7 total -10.0 avg -1.4285714285714286 max 10.0 final 10.0
---
eval # 5
---found goal---
steps 7 total 0.0 avg 0.0 max 10.0 final 10.0
---
eval # 6
---found goal---
steps 8 total -20.0 avg -2.5 max 10.0 final 10.0
---
eval # 7
---found goal---
steps 5 total 10.0 avg 2.0 max 10.0 final 10.0
---
eval # 8
---found goal---
steps 8 total 0.0 avg 0.0 max 10.0 final 10.0
---
eval # 9
---found goal---
steps 8 total -20.0 avg -2.5 max 10.0 final 10.0


# Interactive Mode

Run this to play the game worlds yourself. Actions are:
- `look around`
- `move <north, south, east, west>`
- `open door to  <north, south, east, west>`
- `take <item>`

Type `exit` to quit.

In [ ]:
# Reset the environment
state = reset_dqn(ENV)
cmd = '' # the user's command
# Iterate until the user enters 'exit'
while cmd != 'exit':
  # print the state
  print(state, '\n')
  # get the user's next command
  cmd = input(">> ")
  if cmd != 'exit':
    # execute the user's command
    state, reward, done, infos = ENV.step(cmd)

# Ideas for Bayes Net

- Can you play the game with a Bayes Net? If I have a dataset of features and moves? That seems too simple.
- Could do echo-location. Game maps are arranged on a grid. You could try to echo-locate the coin.

# Ideas for DBN

- Generate text. Do some data crunching to figure out word transition probabilities. Implement a DBN. Run the DBN. But would that confuse the issue with how LLMs work?
- Some sort of prediction. Maybe we have an agent that moves throught the map and you must learn to predict where it will go?

Bigram room description generation

In [ ]:
import numpy as np

In [ ]:
counts = np.zeros([VOCAB.num_words()]*3)
for obs in WORLD_OBSERVATION_HASH.values():
  words = ['SOS'] + normalize_string(obs).split() + ['EOS']
  for i in range(len(words)-2):
    if words[i] in VOCAB._word2index and words[i+1] in VOCAB._word2index  and words[i+2] in VOCAB._word2index:
      counts[VOCAB.word2index(words[i]), VOCAB.word2index(words[i+1]), VOCAB.word2index(words[i+2])] += 1
print(counts.shape)
probs = counts / counts.sum()

(89, 89, 89)


In [ ]:
tokens = [SOS_token,
          np.random.choice(np.indices([VOCAB.num_words()]).squeeze(),
                           p = probs[SOS_token].sum(axis=1) / probs[SOS_token].sum(axis=1).sum())
          ]
words = [VOCAB.index2word(token) for token in tokens]
n = 0
while tokens[-1] != 0 and n < 100:
  next = np.random.choice(np.indices([VOCAB.num_words()]).squeeze(),
                           p = probs[tokens[0],tokens[1]] / probs[tokens[0],tokens[1]].sum())
  words.append(VOCAB.index2word(next))
  tokens = [tokens[1], next]
  n = n + 1
' '.join(words)

'SOS you are in the kitchen . in one part of the room you see a trash can that is closed . in another part of the room you see a trash can that is closed . there is also a workbench that has nothing on it . you also see a clothes line that has nothing on it . to the south you see a dressing table that has nothing on it . through an open sliding patio door to the south you see a clothes line that has nothing on it . you also see a closed wood door .'

# Glove DQN

In [ ]:
import gensim
import gensim.downloader
import numpy as np

In [ ]:
GLOVE = gensim.downloader.load('glove-wiki-gigaword-100')
GLOVE_VOCAB_SIZE = len(GLOVE.key_to_index) #was GLOVE_MODEL.vocab
GLOVE_EMBEDDING_SIZE = 100

In [ ]:
class GloveDQN(nn.Module):

    ### Create all the nodes in the computation graph.
    ### We won't say how to put the nodes together into a computation graph. That is done
    ### automatically when forward() is called.
    def __init__(self, glove, embed_size, num_actions):
        super(GloveDQN, self).__init__()
        self.glove = glove
        self.num_actions = num_actions
        self.embed_size = embed_size
        self.relu1 = nn.LeakyReLU()
        self.linear2 = nn.Linear(embed_size, embed_size//2)
        self.relu3 = nn.LeakyReLU()
        self.linear4 = nn.Linear(embed_size//2, num_actions)

    # Called with either one element to determine next action, or a batch
    # during optimization. Returns tensor([[left0exp,right0exp]...]).
    def forward(self, x):
      h1 = self.relu1(x)
      h2 = self.linear2(h1)
      h3 = self.relu3(h2)
      head = self.linear4(h3)
      return head

In [ ]:
def do_action_dqn(action, env):
  # Execute the action in the environment
  act_obs, act_reward, act_done, act_infos = env.step(action)
  look_obs = act_infos['look'] + '\n' + act_infos['inventory']
  location = obs_location(look_obs)
  inventory = obs_inventory(look_obs)
  if not act_done and 'Unknown' in act_obs or "You can't" in act_obs:
    # Issue negative reward for non-executable actions
    act_reward = -10.0
  elif location == 'corridor' and 'coin' in inventory:
    # Issue higher reward for the coin
    print("---found goal---")
    act_reward = 20.0
    act_done = True
  elif location == 'corridor':
    # Shaped reward for being close to the goal
    act_reward = 10.0
    # act_done = True
  elif location == 'backyard':
    # Shaped reward for being halfway
    act_reward = 5.0
  else:
    # Everything else results in zero reward
    act_reward = 0.0
  #act_reward = act_reward + (10 - 2 * distance(COORDINATES[obs_location(look_obs)], COORDINATES['corridor']))#GOAL_COORDINATES)
  # Generate final observation with inventory
  #final_obs = obs_with_inventory(look_obs, env)
  return look_obs, act_reward, act_done, act_infos

In [ ]:
def state2glove(state):
  words = normalize_string(state).split()
  embedded = [GLOVE[w] for w in words]
  stack = np.stack(embedded)
  final = stack.sum(axis=0)
  return torch.tensor(final).unsqueeze(dim=0)

In [ ]:
def populate_replay_memory_glove(replay_memory, env, actions):
  steps = 0 # total number of steps executed
  # Continue until the buffer is full
  while steps < replay_memory.capacity:
    # Reset the environment
    state = reset_dqn(env)
    # Convert state observation to tokens
    state = state2glove(state).to(DEVICE)
    done = False # Are we done with a trial?
    t = 0 # number of steps in trial
    # Run one trial
    while not done and t < THRESHOLD:
      # Get a random action
      action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
      # increment total steps
      steps = steps + 1
      # increment trial steps
      t = t + 1
      # Execute the action
      next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
      next_state = state2glove(next_state).to(DEVICE)
      reward = torch.tensor([[reward]], device=DEVICE)
      # Push transition information to replay memory
      replay_memory.push(state, action, next_state if not done else None, reward)
      # Get ready for next trial iteration
      state = next_state

In [ ]:
def evaluate_glove(model, env, actions, threshold, epsilon, verbose = True):
  # Reset the game engine
  state = reset_dqn(env)
  if verbose:
    print(state)
  # Convert state observation to tokens
  state = state2glove(state).to(DEVICE)
  t = 0 # The time step
  done = False # Are we done?
  total_reward = 0 # total reward accumulated during run
  max_reward = -float('inf') # highest reward we see during run
  # Loop until done or threshold steps met
  while not done and t < threshold:
    # Epsilon greedy
    if random.random() < epsilon:
      # Use random action
      action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
    else:
      # Use the model
      action = model(state).argmax().view(1, 1)
    if verbose:
      print("action", actions[action.item()])
    # execute the action
    next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
    if verbose:
      print(reward)
      print(next_state)
    # record stats
    total_reward = total_reward + reward
    max_reward = max(max_reward, reward)
    next_state = state2glove(next_state).to(DEVICE)
    # update current state
    state = next_state
    # increment time step
    t = t + 1
  if verbose:
    print("total", total_reward)
  return total_reward, total_reward / t, max_reward, reward, t

In [ ]:
def train_glove(env, actions, epsilon, threshold,
          max_steps, buffer_size, batch_size, gamma, eval_epsilon,
          target_update = 2, num_evals = 10, smoothing = 3):
  steps = 0 # total number of training steps
  current_epsilon = epsilon
  # Create the model
  model = GloveDQN(GLOVE, embed_size = GLOVE_EMBEDDING_SIZE, num_actions = len(actions))
  model.to(DEVICE)
  model.train()
  # initialize the optimizer
  #optimizer = optim.SGD(model.parameters(), lr=0.001)
  optimizer = optim.RMSprop(model.parameters())
  # Initialize target network
  target = GloveDQN(GLOVE, embed_size = GLOVE_EMBEDDING_SIZE, num_actions = len(actions))
  target.load_state_dict(model.state_dict())
  target.to(DEVICE)
  # This keeps the best version of the model we've seen so far
  best = GloveDQN(GLOVE, embed_size = GLOVE_EMBEDDING_SIZE, num_actions = len(actions))
  best.load_state_dict(model.state_dict())
  best.to(DEVICE)
  best.eval()
  # initialize and populate the replay memory
  replay_memory = ReplayMemory(buffer_size)
  populate_replay_memory_glove(replay_memory, env, actions)
  # Keep track of best evaluation reward
  best_eval_reward = -float('inf')
  trial_num = 0
  # For plotting
  plot_train_x = []
  plot_train_y = []
  plot_eval_x = []
  plot_eval_y = []
  # Loop until max training steps reached
  while steps < max_steps:
    # reset the environment
    state = reset_dqn(env)
    # convert state observation to tokens
    state = state2glove(state).to(DEVICE)
    done = False # Are we done?
    trial_total_reward = 0.0 # total trial reward
    best_trial_reward = 0.0 # best trial reward
    t = 0 # number of steps in trial
    print('\nTRIAL', trial_num)
    # Run one trial
    while not done and t < threshold:
      # Epsilon greedy
      if random.random() < current_epsilon:
        # Random action
        action = torch.tensor([[random.randrange(len(actions))]], dtype=torch.long, device=DEVICE)
      else:
        # Use the model to generate an action
        with torch.no_grad():
          action = model(state).argmax().view(1, 1)
      # update epsilon
      current_epsilon = epsilon - (epsilon * (steps / max_steps))
      # increment total training steps
      steps = steps + 1
      # increment trial steps
      t = t + 1
      # execute the action
      next_state, reward, done, infos = do_action_dqn(actions[action.item()], env)
      # keep track of stats
      best_trial_reward = max(best_trial_reward, reward)
      trial_total_reward = trial_total_reward + reward
      # convert state observation to tokens
      next_state = state2glove(next_state).to(DEVICE)
      # Create tensor of reward
      reward = torch.tensor([[reward]], device=DEVICE)
      # Push transition to memory
      replay_memory.push(state, action, next_state if not done else None, reward)
      # update state for next trial iteration
      state = next_state
      # TRAINING:
      # Sample replay memory
      transitions = replay_memory.sample(batch_size)
      # Build a batch
      batch = Transition(*zip(*transitions))
      states_batch = torch.cat(batch.state)
      actions_batch = torch.cat(batch.action)
      rewards_batch = torch.cat(batch.reward)
      # Which transitions are non-terminal?
      non_final_mask = torch.tensor(tuple(map(lambda s: s is not None, batch.next_state)), dtype=torch.bool, device=DEVICE)
      # Next states batch might be smaller than state batch if there are terminal transitions
      next_states_batch = torch.cat([s for s in batch.next_state if s is not None])
      # Get q-values for the actions executed
      state_action_values = model(states_batch).gather(1, actions_batch)
      # Initialize q-values for the next state to all zeros
      next_state_values = torch.zeros(BATCH_SIZE, device=DEVICE)
      # Run the target model on next states and fill in the non-terminal rows
      next_state_values[non_final_mask] = target(next_states_batch).max(dim=1)[0]
      next_state_values = next_state_values.unsqueeze(1)
      # Don't gradient descent through the next state values
      next_state_values.detach()
      # Get the expected values for the next states
      expected_state_action_values = rewards_batch + (next_state_values * gamma)
      # Loss is difference from actual state action values and expected state action values
      loss = F.smooth_l1_loss(state_action_values, expected_state_action_values)
      # Back propagate loss
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()
      # Clip gradients if necessary
      for param in model.parameters():
        param.grad.data.clamp_(-1, 1)
      # Update target model
      if steps % target_update == 0:
        target.load_state_dict(model.state_dict())
      # END OF TRIAL LOOP
    # EVALUATION
    print("total training steps", steps, 'epsilon', current_epsilon)
    print("steps", t,
          "total", trial_total_reward,
          "average", trial_total_reward / t,
          "best", best_trial_reward,
          '\n')
    eval_total_reward = 0.0 # evaluate stats
    # Run evaluation a number of times
    for i in range(10):
      # Call evaluation code
      eval_total_r, eval_avg_r, eval_max_r, eval_final_r, eval_steps = evaluate_glove(model, env, actions, threshold, epsilon=eval_epsilon, verbose=False)
      print('eval #:', i,
            'steps', eval_steps,
            'total', eval_total_r,
            'avg', eval_avg_r,
            'max', eval_max_r)
      eval_total_reward = eval_total_reward + eval_avg_r
    # Plot eval stats for the training trial and the evaluations
    plot_train_x.append(steps)
    plot_eval_x.append(steps)
    plot_eval_y.append(eval_total_reward / 10)
    plot_train_y.append(trial_total_reward / t)
    plt.plot(plot_train_x, smooth(plot_train_y, smoothing=smoothing), label="train")
    plt.plot(plot_eval_x, smooth(plot_eval_y, smoothing=smoothing), label="eval")
    plt.legend()
    plt.show()
    # increment trial number
    trial_num = trial_num + 1
    # Save the best model
    if (eval_total_reward / t) >= best_eval_reward:
      best_eval_reward = eval_total_reward / t
      best.load_state_dict(model.state_dict())
      print("-----------------NEW BEST-------------------")
  return model, best

In [ ]:
last, best = train_glove(ENV, ACTIONS,
                   epsilon = EPSILON,
                   threshold = THRESHOLD,
                   max_steps = MAX_STEPS,
                   buffer_size = BUFFER,
                   batch_size = BATCH_SIZE,
                   gamma = GAMMA,
                   eval_epsilon = EVAL_EPSILON,
                   target_update = TARGET_UPDATE,
                   num_evals = NUM_EVALS)

In [ ]:
for i in range(NUM_EVALS):
  print('---')
  print('eval #', i)
  total_r, avg_r, max_r, final_r, steps = evaluate_glove(best, ENV, ACTIONS,
                                                   threshold = THRESHOLD,
                                                   epsilon = EVAL_EPSILON,
                                                   verbose = False)
  print('steps', steps,
        'total', total_r,
        'avg', avg_r,
        'max', max_r,
        'final', final_r)

---
eval # 0
steps 25 total 97.5 avg 3.9 max 10.0 final -10.0
---
eval # 1
steps 25 total 205.0 avg 8.2 max 10.0 final 10.0
---
eval # 2
---found goal---
steps 16 total 100.0 avg 6.25 max 20.0 final 20.0
---
eval # 3
---found goal---
steps 15 total 135.0 avg 9.0 max 20.0 final 20.0
---
eval # 4
steps 25 total 137.5 avg 5.5 max 10.0 final 10.0
---
eval # 5
---found goal---
steps 24 total 167.5 avg 6.979166666666667 max 20.0 final 20.0
---
eval # 6
steps 25 total 165.0 avg 6.6 max 10.0 final 10.0
---
eval # 7
steps 25 total 125.0 avg 5.0 max 10.0 final 10.0
---
eval # 8
steps 25 total 145.0 avg 5.8 max 10.0 final 10.0
---
eval # 9
steps 25 total 200.0 avg 8.0 max 10.0 final 10.0


In [ ]:
state = reset_dqn(ENV)
print(state)
for a in ['look around', 'open door to south', 'open door to west', 'move south', 'open door to east', 'move north', 'move south', 'move north', 'move west', 'move east', 'move south', 'move east', 'take coin']:
  print(a)
  state, r, d, i = do_action_dqn(a, ENV)
  print(state)
  print(r, d, i)

You are in the kitchen. In one part of the room you see a stove. There is also an oven. You also see a fridge that is closed. In another part of the room you see a counter, that has nothing on it. In one part of the room you see a kitchen cupboard that is closed. There is also a cutlery drawer that is closed. You also see a trash can that is closed. In another part of the room you see a dishwasher that is closed. In one part of the room you see a dining chair, that has nothing on it. 
To the South you see a closed sliding patio door. To the West you see a closed frosted-glass door. 
Inventory (maximum capacity is 2 items): 
  Your inventory is currently empty.

look around
You are in the kitchen. In one part of the room you see a stove. There is also an oven. You also see a fridge that is closed. In another part of the room you see a counter, that has nothing on it. In one part of the room you see a kitchen cupboard that is closed. There is also a cutlery drawer that is closed. You als

In [ ]:
obs_location(state) == 'corridor' and 'coin' in obs_inventory(state)

True